In [1]:
!export TESSDATA_PREFIX=/usr/share/tessdata

In [2]:
import re
import fitz
import pickle
import pandas as pd
from logutils import get_logger
from selenium.webdriver.common.by import By
from exam_question_downloader.scraping.tools import initialize_webdriver, incremental_retry, do_with_delayed_retry, match_patterns
from exam_question_downloader.scraping.navigation import magic_directories_journey
from exam_question_downloader.utils.consts import SOURCE_URLS, OUTPUT_PATH, ROOT_DIR, SUBJECTS_PATTERNS
from exam_question_downloader.utils.text_processing import get_text_docs_from_dir, extract_questions_from_doc

In [3]:
logger = get_logger("YEA")

# Scraping

In [3]:
browser = initialize_webdriver(use_browser=True)

In [4]:
for url in SOURCE_URLS:
    magic_directories_journey(url, browser)

[2024-05-04 12:27:17,071] | INFO | navigation.py:magic_directories_journey:17 | Visiting https://www.upv.es/entidades/SRH/pas/676960normalc.html
[2024-05-04 12:27:18,667] | INFO | navigation.py:magic_directories_journey:17 | Visiting https://www.upv.es/entidades/SRH/pas/1233760normalc.html
[2024-05-04 12:27:18,980] | INFO | navigation.py:magic_directories_journey:17 | Visiting https://www.upv.es/entidades/SRH/pas/1233157normalc.html
[2024-05-04 12:27:19,250] | INFO | navigation.py:magic_directories_journey:17 | Visiting https://www.upv.es/entidades/SRH/pas/1233108normalc.html
[2024-05-04 12:27:19,518] | INFO | navigation.py:magic_directories_journey:17 | Visiting https://www.upv.es/entidades/SRH/pas/1233104normalc.html
[2024-05-04 12:27:19,909] | INFO | navigation.py:magic_directories_journey:17 | Visiting https://www.upv.es/entidades/SRH/pas/1240455normalc.html
[2024-05-04 12:27:20,130] | INFO | navigation.py:magic_directories_journey:17 | Visiting https://www.upv.es/entidades/SRH/pas

# Text processing

In [4]:
textdocs = get_text_docs_from_dir(OUTPUT_PATH)
textdocs

[2024-05-06 18:50:48,896] | INFO | text_processing.py:get_text_docs_from_dir:86 | File /home/serbaf/Repos/scripts/scraping/exam_question_downloader/output/71d1195a-2122-4366-a22f-3089accdf727.pdf
[2024-05-06 18:50:48,936] | INFO | text_processing.py:get_text_docs_from_dir:86 | File /home/serbaf/Repos/scripts/scraping/exam_question_downloader/output/82c7933d-8ccf-4469-9c77-d9336af34d7e.pdf


[2024-05-06 18:50:48,951] | INFO | text_processing.py:get_text_docs_from_dir:86 | File /home/serbaf/Repos/scripts/scraping/exam_question_downloader/output/b0a998a6-7e92-4c11-9ff5-224545bb9d48.pdf
[2024-05-06 18:50:48,962] | INFO | text_processing.py:get_text_docs_from_dir:86 | File /home/serbaf/Repos/scripts/scraping/exam_question_downloader/output/2769253d-c7f3-4511-acce-54d0e089d1eb.pdf
[2024-05-06 18:50:48,981] | INFO | text_processing.py:get_text_docs_from_dir:86 | File /home/serbaf/Repos/scripts/scraping/exam_question_downloader/output/713e886c-8f0d-40a4-b518-044bcfe5661e.pdf
[2024-05-06 18:50:49,000] | INFO | text_processing.py:get_text_docs_from_dir:86 | File /home/serbaf/Repos/scripts/scraping/exam_question_downloader/output/72b66f9c-894d-4eb1-8560-c407219d644f.pdf
[2024-05-06 18:50:49,080] | INFO | text_processing.py:get_text_docs_from_dir:86 | File /home/serbaf/Repos/scripts/scraping/exam_question_downloader/output/c139c621-91d7-4487-9f3b-f15d8853a6cc.pdf
[2024-05-06 18:50:49

[('71d1195a-2122-4366-a22f-3089accdf727.pdf',
  " \nACUERDO del tribunal de selección de las pruebas selectivas de acceso al grupo A, subgrupo \nA2, sector administración especial, categoría de ayudante de archivos, biblioteca y museos, \npor el sistema de concurso-oposición (Código: 2022/P/FC/C/1),  \n \n \nReunido el órgano técnico de selección se acuerda el cambio de lugar de celebración del \nprimer ejercicio de estas pruebas selectivas, que tendrá lugar el 30 de junio de 2023, a las 10:00 \nhoras. La nueva localización será: \n \n \n \nLugar de realización del primer ejercicio \nAula 234 de la Escuela Técnica Superior de \nIngeniería Industrial (Edificio 5H) \n \n \n \n \n \n \n \nValencia, a 15 de junio de 2023 \nLa presidenta del tribunal de selección. Dª. Inmaculada Romero Gil \n \n \n \n \nINMACULADA\n|ROMERO|GIL\nFirmado digitalmente por \nINMACULADA|ROMERO|GIL \nFecha: 2023.06.15 14:16:22 \n+02'00'\n"),
 ('82c7933d-8ccf-4469-9c77-d9336af34d7e.pdf',
  'PRIMER EJERCICIO – DFI 

In [5]:
questiondocs = []
for name, doc in textdocs:
    questiondocs.append((name, extract_questions_from_doc(doc)))
questiondocs

[2024-05-06 18:55:35,451] | INFO | text_processing.py:extract_questions_from_doc:77 | Appending to Question
[2024-05-06 18:55:35,453] | INFO | text_processing.py:extract_questions_from_doc:73 | Appending to Question
[2024-05-06 18:55:35,455] | INFO | text_processing.py:extract_questions_from_doc:70 | Appending to A
[2024-05-06 18:55:35,456] | INFO | text_processing.py:extract_questions_from_doc:63 | Appending to B
[2024-05-06 18:55:35,457] | INFO | text_processing.py:extract_questions_from_doc:56 | Appending to C
[2024-05-06 18:55:35,458] | INFO | text_processing.py:extract_questions_from_doc:49 | Appending to D
[2024-05-06 18:55:35,460] | INFO | text_processing.py:extract_questions_from_doc:38 | Appending to Question
[2024-05-06 18:55:35,461] | INFO | text_processing.py:extract_questions_from_doc:73 | Appending to Question
[2024-05-06 18:55:35,462] | INFO | text_processing.py:extract_questions_from_doc:70 | Appending to A
[2024-05-06 18:55:35,463] | INFO | text_processing.py:extract_q

[('71d1195a-2122-4366-a22f-3089accdf727.pdf', []),
 ('82c7933d-8ccf-4469-9c77-d9336af34d7e.pdf', []),
 ('b0a998a6-7e92-4c11-9ff5-224545bb9d48.pdf', []),
 ('2769253d-c7f3-4511-acce-54d0e089d1eb.pdf', []),
 ('713e886c-8f0d-40a4-b518-044bcfe5661e.pdf', []),
 ('72b66f9c-894d-4eb1-8560-c407219d644f.pdf',
  [{'question': '1. ¿Cuál de los siguientes principios NO se recoge en el artículo 2 de la Constitución Española de 1978?: ',
    'a': 'a. Solidaridad. ',
    'b': 'b. Subsidiariedad. ',
    'c': 'c. Unidad. ',
    'd': 'd. Autonomía. '},
   {'question': '2. Según la Ley Orgánica 3/2007 (artículo 24), ¿cómo garantizarán las administraciones educativas el igual derecho a la educación de mujeres y hombres?:  ',
    'a': 'a. A través de la presencia equilibrada de mujeres y hombres docentes en todas las etapas educativas. ',
    'b': 'b. A través de la integración real de mujeres y hombres en los cargos intermedios educativos. ',
    'c': 'c. A través de la integración activa, en los objetivos

In [4]:
ASSETS_DIR = ROOT_DIR.joinpath("assets")
# ASSETS_DIR.mkdir(exist_ok=True)
# ASSETS_DIR.joinpath("questiondocs.pkl").write_bytes(pickle.dumps(questiondocs))

questiondocs = pickle.loads(ASSETS_DIR.joinpath("questiondocs.pkl").read_bytes())

questiondocs

[('71d1195a-2122-4366-a22f-3089accdf727.pdf', []),
 ('82c7933d-8ccf-4469-9c77-d9336af34d7e.pdf', []),
 ('b0a998a6-7e92-4c11-9ff5-224545bb9d48.pdf', []),
 ('2769253d-c7f3-4511-acce-54d0e089d1eb.pdf', []),
 ('713e886c-8f0d-40a4-b518-044bcfe5661e.pdf', []),
 ('72b66f9c-894d-4eb1-8560-c407219d644f.pdf',
  [{'question': '1. ¿Cuál de los siguientes principios NO se recoge en el artículo 2 de la Constitución Española de 1978?: ',
    'a': 'a. Solidaridad. ',
    'b': 'b. Subsidiariedad. ',
    'c': 'c. Unidad. ',
    'd': 'd. Autonomía. '},
   {'question': '2. Según la Ley Orgánica 3/2007 (artículo 24), ¿cómo garantizarán las administraciones educativas el igual derecho a la educación de mujeres y hombres?:  ',
    'a': 'a. A través de la presencia equilibrada de mujeres y hombres docentes en todas las etapas educativas. ',
    'b': 'b. A través de la integración real de mujeres y hombres en los cargos intermedios educativos. ',
    'c': 'c. A través de la integración activa, en los objetivos

In [5]:
aux = []
for name, qd in questiondocs:
    if len(qd) > 0:
        for q in qd:
            if match_patterns(q["question"], SUBJECTS_PATTERNS):
                q["doc"] = name
                aux.append(q)
    else:
        pass
df = pd.DataFrame(aux)
df.reset_index(drop=True)

question  \
0   1. ¿Cuál de los siguientes principios NO se re...   
1   2. Según la Ley Orgánica 3/2007 (artículo 24),...   
2   3. Según el artículo 4 de la Ley Orgánica 1/20...   
3   5. Según la Ley 4/2021, de 16 de abril, de la ...   
4   6. ¿Cuál de las siguientes respuestas es corre...   
5   7. ¿Cuál es el órgano encargado de aprobar la ...   
6   8. En las elecciones a Rector/a, según los Est...   
7   19. De acuerdo con la normativa de acceso a la...   
8   1.. Según la Ley 31/1995, de 8 de noviembre, d...   
9   1. La autonomía de las universidades se recono...   
10  5. Según la Ley de la Función Pública Valencia...   
11  76. El artículo 22 de la Ley Orgánica 3/2007 p...   
12  3) Según la Ley 4/2021, de 16 de abril, de la ...   
13  4) Según el Artículo 6 de la Ley Orgánica del ...   
14  5) Señale la respuesta FALSA, según el Artícul...   
15  7) Según el artículo 9 de la Ley 1/2022, de 13...   
16  8) Según el artículo 4 de la ley 31/1995, de 8...   
17  27. Daniel Isenberg, Profesor de Babson Colleg...   
18  45. Según la Ley Orgánica del Sistema Universi...   
19  1) ¿Cuál es la forma política del Estado españ...   
20  3) ¿Qué se garantiza en el ámbito del empleo p...   
21  4) Según el objeto de la Ley Orgánica 1/2004, ...   
22  5) Según la Ley de Función Pública Valenciana,...   
23  6) ¿Cuál de los siguientes derechos del person...   
24  7) ¿Quién tiene la potestad para aprobar la re...   
25  8) ¿Cuál de los siguientes NO es un derecho de...   
26  84) ¿Cuál es el órgano de participación de la ...   
27  1. Según la Ley 31/1995, de 8 de noviembre, de...   
28  9. ¿Qué órgano de la UPV es el encargado de ap...   
29  14. De acuerdo con los Estatutos vigentes, la ...   
30  22. Según el art. 98 de la Ley 4/2021, de 16 d...   
31  59. Según el artículo 1 de los Estatutos de la...   
32  1. Según la Constitución Española se reconoce ...   
33  2. Según el Estatuto de Autonomía de la Comuni...   
34  3. Según la Ley de la Función Pública Valencia...   
35  5. ¿Cuáles serían los centros encargados en la...   
36  6. Según los Estatutos de la Universitat Polit...   
37  7. Según el art. 42 de los Estatutos de la Uni...   
38  10. Según la Ley 31/1995, de 8 de noviembre, d...   
39  11. La Universitat Politècnica de València, en...   
40  13. Según la Ley Orgánica 1/2004, de 28 de dic...   
41  2. Según la Ley 4/2021 de la ordenación y gest...   
42  3. La Colaboración con otras entidades o perso...   
43  8. Según la Constitución Española de 1978 (art...   
44  9. La Constitución Española de 1978 indica que...   
45  49. El Artículo 30 de la LOSU. Cooperación int...   

                                                    a  \
0                                    a. Solidaridad.    
1   a. A través de la presencia equilibrada de muj...   
2   a. El respeto de los derechos y libertades fun...   
3   a. Dentro de los dos meses siguientes desde la...   
4   a. Solo afecta a las empresas, no se aplica en...   
5                         a. El Consejo de Gobierno.    
6                                            a. 21%     
7   a. Para titulados conforme a sistemas educativ...   
8   a) Se entenderá por «condición de trabajo» el ...   
9                                              a. 15    
10  a. Quien desarrolla funciones directivas profe...   
11  a. Con el fin de avanzar hacia un reparto equi...   
12  a. Personal funcionario de carrera, personal f...   
13  a. La docencia, preferentemente presencial, po...   
14  a. Los estudios de Grado tienen como finalidad...   
15  a. Se deben cumplir los principios de protecci...   
16                                    a. Enfermedad.    
17     a) Los nombres de los empleados de la empresa.   
18                                   a) Elarticulos!.   
19                          A) Monarquía Democrática    
20   A) Igualdad de salarios entre hombres y mujeres    
21             A) La violencia física sobre la mujer    
22                                A) Servicio activo  

In [6]:
df.to_csv(ASSETS_DIR.joinpath("preguntas_leyes.csv"), index=False)

In [10]:
df["doc"].unique()

array(['72b66f9c-894d-4eb1-8560-c407219d644f.pdf',
       '41a1940c-17eb-471b-a9e1-5629a545832a.pdf',
       '61cb9c36-3c45-4499-8613-6930bb7b4243.pdf',
       '170172c0-b03e-4425-86f1-b09eb183cef8.pdf',
       '812043ae-d82d-4c91-9405-782ec4a28d98.pdf',
       '65d48b47-d62f-4a51-8f84-205558243daf.pdf',
       'ed96d540-86d4-431c-ad9e-db78ef7f355c.pdf',
       'b4d331e2-2660-4d5d-a587-9ad18f31a49d.pdf',
       'a7eab3e6-5981-49b1-b534-b4df9a0546db.pdf'], dtype=object)

In [9]:
doc_id = "41a1940c-17eb-471b-a9e1-5629a545832a.pdf"

In [10]:
df[df["doc"] == doc_id]

question  \
8  1.. Según la Ley 31/1995, de 8 de noviembre, d...   

                                                   a  \
8  a) Se entenderá por «condición de trabajo» el ...   

                                                   b  \
8  b) Ea Secretario/a de la escuela) EV/a Directo...   

                                                   c  \
8  c) Defensa de las singularidades culturales de...   

                                          d  \
8  d) Ninguna de las anteriores es correcta   

                                        doc  
8  41a1940c-17eb-471b-a9e1-5629a545832a.pdf

In [12]:
textdocs

NameError: name 'textdocs' is not defined

In [11]:
doc = [x for x in questiondocs if x[0] == doc_id][0][1]
for question in doc:
    print(question)

{'question': '1.. Según la Ley 31/1995, de 8 de noviembre, de prevención de Riesgos Laborales, ensu Artículo 4.', 'a': 'a) Se entenderá por «condición de trabajo» el conjunto de actividades omedidas adoptadas o previstas en todas las fases de actividad de la empresa-on el fn de evitr 0 disminuir ls riesgos derivados del trabajo1) Se entenderá por «prevención» el conjunto de actividades o medidasadoptadas o previstas en todas las fases de actividad de la empresa con el finde evitar o disminuir los riesgos derivados del trabajo) Se entenderá por «daños derivados del trabajo» el conjunto de actvidades omedidas adoptadas o previstas en todas las fases de actividad de la empresacon el fin de evitar o disminuir los riesgos derivados del tabajo) Se entenderá por «equipo de trabajo» el conjunto de actividades o medidasadoptadas o previstas en todas la fases de actividad de la empresa con el finde evitar o disminuir os riesgos derivados del trabajoEl Consejo de Departamento será presidido por:a

In [57]:
from exam_question_downloader.utils.consts import RGX4, RGX6

In [66]:
rgx = RGX6
text = doc[4]["question"]

In [67]:
RGX6.pattern

'.*(LOSU)|([Ss]istema [Uu]niversitario).*'

In [68]:
text

'5) Señale la respuesta FALSA, según el Artículo 9 de la Ley Orgánica del Sistema Universitario. '

In [70]:
RGX6.match(text)

In [72]:
re.compile(r'.*((LOSU)|([Ss]istema [Uu]niversitario)).*').match(text)

<re.Match object; span=(0, 96), match='5) Señale la respuesta FALSA, según el Artículo 9>